In [60]:
import pandas as pd
import numpy as np
import torch

In [61]:
ercot_2022_actual_load_df = pd.read_csv('downloaded/20220101-20221212 ERCOT Actual Load.csv')
ercot_2022_actual_load_df.head(), ercot_2022_actual_load_df.tail()

(                   Date      Load
 0  1/1/2022 12:00:00 AM  38145.79
 1   1/1/2022 1:00:00 AM  37158.13
 2   1/1/2022 2:00:00 AM  35966.24
 3   1/1/2022 3:00:00 AM  35148.96
 4   1/1/2022 4:00:00 AM  34610.33,
                         Date      Load
 8299   12/12/2022 7:00:00 PM  46775.92
 8300   12/12/2022 8:00:00 PM  46217.27
 8301   12/12/2022 9:00:00 PM  44998.13
 8302  12/12/2022 10:00:00 PM  42774.80
 8303  12/12/2022 11:00:00 PM  40435.58)

In [266]:

def train_test_split(df, test_size=0.21):
    train_size = int(len(df) * (1 - test_size))
    train_set = df[:train_size]
    test_set = df[train_size:]
    return train_set, test_set

def train_test_split_by_date(df):
    train_set = df[df['Date'] < '1/1/2022']
    test_set = df[df['Date'] >= '1/1/2022']
    return train_set, test_set

ercot_2022_actual_load_df['Date'] = pd.to_datetime(ercot_2022_actual_load_df['Date'])
load_input_target = ercot_2022_actual_load_df
train_set, test_set = train_test_split(ercot_2022_actual_load_df)
train_set.shape, test_set.shape

((6560, 2), (1744, 2))

In [256]:
class TimeseriesDataset(torch.utils.data.Dataset):   
    def __init__(self, X, y, seq_len=1):
        self.X = X
        self.y = y
        self.seq_len = seq_len

    def __len__(self):
        return self.X.__len__() #- (self.seq_len-1)

    def __getitem__(self, index):
        #print(index)
        a, b = self.X[index:index+self.seq_len], self.y[index+self.seq_len]
        #print(a.shape, b.shape)
        return a, b

In [257]:
# def df_to_tensor(df):
#     X = torch.tensor(df['Load'].values).float()
#     return X
# #print(test_set.values[1663])
# print(train_set['Date'].shape, train_set['Load'].shape)

# def to_date_array(da):
#     da = pd.to_datetime(da)
#     return da.apply(lambda x : x.timestamp())

# train_date_array = to_date_array(train_set['Date'])
# test_date_array = to_date_array(test_set['Date'])
# #print(train_date_array.shape, test_date_array.shape)
# def expand_dims(da):
#     return np.expand_dims(da, axis = 1)
# for i in [train_date_array, test_date_array, train_set['Load'], test_set['Load']]:
#     i = expand_dims(i)
#     print(i.shape)
# x_time_series_with_datetime = np.concatenate((train_date_array, train_set['Load']), axis=1)
# y_time_series_with_datetime = np.concatenate((test_date_array, test_set['Load']), axis=1)
# #x_time_series = df_to_tensor(train_set)
# #y_time_series = df_to_tensor(test_set)

# x_time_series_with_datetime, y_time_series_with_datetime

In [258]:
def df_to_tensor(df):
    X = torch.tensor(df[['Date','Load']].values).float()
    return X

def to_date_array(da):
    da = pd.to_datetime(da)
    return da.apply(lambda x : x.timestamp())

train_set['Date'] = to_date_array(train_set['Date'])
test_set['Date'] = to_date_array(test_set['Date'])

x_time_series = df_to_tensor(train_set)
y_time_series = df_to_tensor(test_set)

def datetime_tensorfy(df):
    df['Date'] = to_date_array(df['Date'])
    return df_to_tensor(df)

time_series_with_datetime = datetime_tensorfy(train_set)



/tmp/ipykernel_1217984/316794197.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_1217984/316794197.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [259]:
x_time_series, y_time_series

(tensor([[1.6410e+00, 3.8146e+04],
         [1.6410e+00, 3.7158e+04],
         [1.6410e+00, 3.5966e+04],
         ...,
         [1.6646e+00, 3.4497e+04],
         [1.6646e+00, 3.5098e+04],
         [1.6646e+00, 3.6540e+04]]),
 tensor([[1.6646e+00, 3.8599e+04],
         [1.6646e+00, 4.0594e+04],
         [1.6646e+00, 4.2461e+04],
         ...,
         [1.6709e+00, 4.4998e+04],
         [1.6709e+00, 4.2775e+04],
         [1.6709e+00, 4.0436e+04]]))

In [263]:
seq_len = 73
batch_size = seq_len*2
train_dataset = TimeseriesDataset(x_time_series, y_time_series, seq_len=seq_len)

train_loader = torch.utils.data.DataLoader(train_dataset, batch_size = batch_size, shuffle = False)

for nth_batch, (batch, _) in enumerate(train_dataset):
    print(f'Batch {nth_batch}:')
    print(f'batch shape: {batch.shape}')
    print(f'batch: {batch}')


Batch 0:
batch shape: torch.Size([73, 2])
batch: tensor([[1.6410e+00, 3.8146e+04],
        [1.6410e+00, 3.7158e+04],
        [1.6410e+00, 3.5966e+04],
        [1.6410e+00, 3.5149e+04],
        [1.6410e+00, 3.4610e+04],
        [1.6410e+00, 3.4451e+04],
        [1.6410e+00, 3.4569e+04],
        [1.6410e+00, 3.4632e+04],
        [1.6410e+00, 3.5562e+04],
        [1.6410e+00, 3.7847e+04],
        [1.6410e+00, 3.9936e+04],
        [1.6410e+00, 4.1791e+04],
        [1.6410e+00, 4.3130e+04],
        [1.6410e+00, 4.3992e+04],
        [1.6410e+00, 4.4248e+04],
        [1.6410e+00, 4.4209e+04],
        [1.6411e+00, 4.4333e+04],
        [1.6411e+00, 4.4944e+04],
        [1.6411e+00, 4.6103e+04],
        [1.6411e+00, 4.5951e+04],
        [1.6411e+00, 4.5761e+04],
        [1.6411e+00, 4.5529e+04],
        [1.6411e+00, 4.4828e+04],
        [1.6411e+00, 4.3891e+04],
        [1.6411e+00, 4.2904e+04],
        [1.6411e+00, 4.2179e+04],
        [1.6411e+00, 4.2061e+04],
        [1.6411e+00, 4.2491e+04],

In [264]:
import torch
import torch.nn as nn
dims = 2
print(dims)

class Transformer(nn.Module):
  def __init__(self, input_dim, output_dim, hidden_dim, num_layers, num_heads):
    super(Transformer, self).__init__()

    self.encoder = nn.TransformerEncoder(
      nn.TransformerEncoderLayer(input_dim, num_heads, hidden_dim),
      num_layers
    )

    self.decoder = nn.TransformerDecoder(
      nn.TransformerDecoderLayer(output_dim, num_heads, hidden_dim),
      num_layers
    )

    self.output_layer = nn.Linear(hidden_dim, output_dim)

  def forward(self, src, trg):
    context = self.encoder(src)
    output = self.decoder(trg, context)
    return self.output_layer(output)

my_transformer = Transformer(input_dim=dims, output_dim=dims, hidden_dim=dims, num_layers=4, num_heads=1)

2


In [265]:
from tqdm import tqdm
import os
def train_transformer(model, train_loader, epochs):
  criterion = nn.MSELoss()
  optimizer = torch.optim.Adam(model.parameters(), lr=0.05)

  for epoch in range(epochs):
    for batch, _ in tqdm(train_loader):
      #print(batch.shape)
      #batch2 = batch.transpose(-2, -1)

      #print(batch.shape)
      output = model(batch, batch)
      loss = criterion(output, batch)
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()
    print(f'Epoch {epoch+1}, Loss: {loss.item():.4f}')


if os.path.exists('transformer_model.pt'):
  my_transformer = torch.load('transformer_model.pt')
  my_transformer.eval()
  
else:    
    train_transformer(my_transformer, train_loader, epochs=20)
    torch.save(my_transformer, 'transformer_model.pt')

 24%|██▍       | 11/45 [00:04<00:13,  2.61it/s]


IndexError: index 1744 is out of bounds for dimension 0 with size 1744

In [ ]:

torch.save(my_transformer, 'transformer_model.pt')

In [ ]:
test_set.head()

Date      Load
1416  3/1/2022 12:00:00 AM  39160.63
1417   3/1/2022 1:00:00 AM  39231.70
1418   3/1/2022 2:00:00 AM  39618.57
1419   3/1/2022 3:00:00 AM  40554.77
1420   3/1/2022 4:00:00 AM  42273.99

In [ ]:
def test_transformer(model, test_loader):
  with torch.no_grad():
    for batch, _ in test_loader:
      #batch = batch.permute(1, 0, 2)
      output = model(batch, batch)
      print(f'Input: {batch}')
      print(f'Output: {output}')
test_transformer(my_transformer, train_loader)

Input: tensor([[38145.7891, 37158.1289, 35966.2383,  ..., 47228.4492, 45556.1602,
         44433.3789],
        [37158.1289, 35966.2383, 35148.9609,  ..., 45556.1602, 44433.3789,
         43952.7617],
        [35966.2383, 35148.9609, 34610.3281,  ..., 44433.3789, 43952.7617,
         43942.2891],
        ...,
        [47228.4492, 45556.1602, 44433.3789,  ..., 51080.6797, 50412.4219,
         48836.8789],
        [45556.1602, 44433.3789, 43952.7617,  ..., 50412.4219, 48836.8789,
         47552.0586],
        [44433.3789, 43952.7617, 43942.2891,  ..., 48836.8789, 47552.0586,
         46701.8906]])
Output: tensor([[44193.4844, 44191.8555, 44186.4141,  ..., 44076.5742, 44072.4492,
         44073.0547],
        [44256.2930, 44251.2578, 44247.4023,  ..., 44135.2031, 44132.8789,
         44131.9414],
        [44246.0312, 44242.7344, 44239.1133,  ..., 44126.2656, 44125.8164,
         44121.0898],
        ...,
        [44241.9180, 44238.1641, 44233.7070,  ..., 44122.1250, 44120.9375,
         4

In [ ]:
import plotly.express as px 
def plot_predictions(model, test_loader):
    """Using Plotly, plot predictions of the model on the test set against the actual values for a single batch. The y-axis is 'Load'. The x-axis is the index of the test set."""
    with torch.no_grad():
        for batch, _ in test_loader:
            output = model(batch, batch)
            output = output.flatten()
            batch = batch.flatten()
            df = pd.DataFrame({'Load': output, 'Predicted Load': batch})
            df = df.reset_index()
            df = df.melt(id_vars='index', value_vars=['Actual Load', 'Predicted Load'])
            fig = px.line(df, x='index', y='value', color='variable')
            ax = fig.update_xaxes(title='Datetime')
            ax = fig.update_yaxes(title='Load')
            fig.update_layout(title='Predictions vs Actuals')

            fig.show()
            break
plot_predictions(my_transformer, train_loader)


In [ ]:
def summarize_transformer(model):
  print(model)
summarize_transformer(Transformer)

<class '__main__.Transformer'>
